In [1]:
# This is necessary to recognize the modules
import os
import sys
from decimal import Decimal
import warnings

warnings.filterwarnings("ignore")

root_path = os.path.abspath(os.path.join(os.getcwd(), '../..'))
sys.path.append(root_path)

In [2]:
from core.backtesting import BacktestingEngine

backtesting = BacktestingEngine(root_path=root_path, load_cached_data=False)

In [3]:
from hummingbot.strategy_v2.executors.position_executor.data_types import TrailingStop
from controllers.directional_trading.smugplug import SmugPlugControllerConfig
import datetime
from decimal import Decimal


# Controller configuration
connector_name = "binance"
trading_pair = "WLD-USDT"
interval = "1h"
macd_fast = 21
macd_slow = 42
macd_signal = 9
total_amount_quote = 1000
max_executors_per_side = 3
take_profit = 0.23
stop_loss = 0.02
trailing_stop_activation_price = 0.009
trailing_stop_trailing_delta = 0.00171
time_limit = 60 * 60 * 24 * 2
cooldown_time = 60 * 15
atr_length = 11
atr_multiplier = 1.5
short_ema = 8
medium_ema = 29
long_ema = 31


# Creating the instance of the configuration and the controller
config = SmugPlugControllerConfig(
    connector_name=connector_name,
    trading_pair=trading_pair,
    interval=interval,
    macd_fast=macd_fast,
    macd_slow=macd_slow,
    macd_signal=macd_signal,
    ema_short=short_ema,
    ema_medium=medium_ema,
    ema_long=long_ema,
    atr_length=atr_length,
    atr_multiplier=atr_multiplier,
    total_amount_quote=Decimal(total_amount_quote),
    take_profit=Decimal(take_profit),
    stop_loss=Decimal(stop_loss),
    trailing_stop=TrailingStop(activation_price=Decimal(trailing_stop_activation_price), trailing_delta=Decimal(trailing_stop_trailing_delta)),
    time_limit=time_limit,
    max_executors_per_side=max_executors_per_side,
    cooldown_time=cooldown_time,
)

In [4]:
# Running the backtesting this will output a backtesting result object that has built in methods to visualize the results

start = int(datetime.datetime(2025, 1, 1).timestamp())
end = int(datetime.datetime(2025, 3, 17).timestamp())


backtesting_result = await backtesting.run_backtesting(config, start, end, "1m")

2025-03-18 14:59:05,677 - asyncio - ERROR - Unclosed client session
client_session: <aiohttp.client.ClientSession object at 0x724db39cba60>
2025-03-18 14:59:05,679 - asyncio - ERROR - Unclosed connector
connections: ['deque([(<aiohttp.client_proto.ResponseHandler object at 0x724db39d8b20>, 153650.240252146)])']
connector: <aiohttp.connector.TCPConnector object at 0x724db39cb2e0>
2025-03-18 14:59:52,903 - asyncio - ERROR - Unclosed client session
client_session: <aiohttp.client.ClientSession object at 0x724db2317cd0>
2025-03-18 14:59:52,906 - asyncio - ERROR - Unclosed connector
connections: ['deque([(<aiohttp.client_proto.ResponseHandler object at 0x724db29e7d60>, 153697.311576651)])']
connector: <aiohttp.connector.TCPConnector object at 0x724db2317850>
2025-03-18 14:59:54,455 - asyncio - ERROR - Unclosed client session
client_session: <aiohttp.client.ClientSession object at 0x724db23555d0>
2025-03-18 14:59:54,459 - asyncio - ERROR - Unclosed connector
connections: ['deque([(<aiohttp.c

In [5]:
# Let's see what is inside the backtesting results
print(backtesting_result.get_results_summary())
backtesting_result.get_backtesting_figure()


Net PNL: $1521.69 (152.17%) | Max Drawdown: $-129.75 (-12.91%)
Total Volume ($): 1446666.67 | Sharpe Ratio: 3.03 | Profit Factor: 1.37
Total Executors: 2170 | Accuracy Long: 0.71 | Accuracy Short: 0.74
Close Types: Take Profit: 0 | Stop Loss: 587 | Time Limit: 1 |
             Trailing Stop: 1582 | Early Stop: 0



In [ ]:
# 2. The executors dataframe: this is the dataframe that contains the information of the orders that were executed
import pandas as pd

executors_df = backtesting_result.executors_df
executors_df.head()

### Backtesting Analysis

### Scatter of PNL per Trade
This bar chart illustrates the PNL for each individual trade. Positive PNLs are shown in green and negative PNLs in red, providing a clear view of profitable vs. unprofitable trades.


In [ ]:
import plotly.express as px

# Create a new column for profitability
executors_df['profitable'] = executors_df['net_pnl_quote'] > 0

# Create the scatter plot
fig = px.scatter(
    executors_df,
    x="timestamp",
    y='net_pnl_quote',
    title='PNL per Trade',
    color='profitable',
    color_discrete_map={True: 'green', False: 'red'},
    labels={'timestamp': 'Timestamp', 'net_pnl_quote': 'Net PNL (Quote)'},
    hover_data=['filled_amount_quote', 'side']
)

# Customize the layout
fig.update_layout(
    xaxis_title="Timestamp",
    yaxis_title="Net PNL (Quote)",
    legend_title="Profitable",
    font=dict(size=12, color="white"),
    showlegend=False,
    plot_bgcolor='rgba(0,0,0,0.8)',  # Dark background
    paper_bgcolor='rgba(0,0,0,0.8)',  # Dark background for the entire plot area
    xaxis=dict(gridcolor="gray"),
    yaxis=dict(gridcolor="gray")
)

# Add a horizontal line at y=0 to clearly separate profits and losses
fig.add_hline(y=0, line_dash="dash", line_color="lightgray")

# Show the plot
fig.show()

### Histogram of PNL Distribution
The histogram displays the distribution of PNL values across all trades. It helps in understanding the frequency and range of profit and loss outcomes.


In [ ]:
fig = px.histogram(executors_df, x='net_pnl_quote', title='PNL Distribution')
fig.show()


# Conclusion
We can see that the indicator has potential to bring good signals to trade and might be interesting to see how we can design a market maker that shifts the mid price based on this indicator.
A lot of the short signals are wrong but if we zoom in into the loss signals we can see that the losses are not that big and the wins are bigger and if we had implemented the trailing stop feature probably a lot of them are going to be profits.

# Next steps
- Filter only the loss signals and understand what you can do to prevent them
- Try different configuration values for the indicator
- Test in multiple markets, pick mature markets like BTC-USDT or ETH-USDT and also volatile markets like DOGE-USDT or SHIB-USDT